In [1]:
import numpy as np
import qrotate as qr

# Generate a big rectangular prism with randomised orientation and centre of mass

Sample some random points in a plane by flattening out one coordinate, then translate half to the positive face (+1) and half to the negative face (-1). Do it two more times and you have a cube. It can be rotated with the quaternion method from part 1


In [2]:
import plotly
import plotly.graph_objs as go
def plotly_scatter(pointsets, sizes):
    """Plots some 3d point clouds. Usage: plotly_scatter([pointset1, pointset2], [size1, size2])"""
    data = []
    for p, s in zip(pointsets, sizes):
        a,b,c = p[:,0], p[:,1], p[:,2]
        trace = go.Scatter3d(x=a, y=b, z=c, mode='markers', marker={'size': s,'opacity': 0.8,})
        data.append(trace)
    layout = go.Layout(margin={'l': 0, 'r': 0, 'b': 0, 't': 0})
    plot_figure = go.Figure(data=data, layout=layout)
    plotly.offline.iplot(plot_figure)

def random_cube(num_pts):
    pts = []
    for a in range(3):
        zero_axis = np.array([1,1,1])
        zero_axis[a] = 0
        #make a plane of points:
        pt = np.random.uniform(-1, 1, [num_pts,3] )
        pt = pt*zero_axis
        #zoom popints to the cube faces:
        pt = pt + np.random.choice([-1,1], [num_pts])[:,None] * (1-zero_axis)
        pts.append(pt)
        
    return np.vstack(pts)

In [3]:
rect = random_cube(1500) * np.array([2, 4, 1]) + 3

#now rotate by a random quaternion:
q = np.random.uniform(-1,1, [4])
nq = qr.fast_normalise(q)
rect = rect.dot(qr.quaternion_rotation_matrix(nq))

#plot;
plotly_scatter([rect], [3])

# Calculate some geometric properties before aligning.

Alignment could be done by doing a PCA over the point coordinates - as in [here](https://alyssaq.github.io/2015/computing-the-axes-or-orientation-of-a-blob/) - but this requires calculating a covariance matrix which is a little slow. It's also unnecessary. Instead, we can give the points mass and calculate the 'moment of inertia' tensor, which is just a `3x3` array (the coordinates covariance matrix would have been `npoints x npoints`). Then, like PCA would do, calculate the eigendecomposition on that. 

First step is to calculate the moment of inertia. I used the explicit form of what `mdtraj` does using `np.einsum` ([see here](https://github.com/mdtraj/mdtraj/blob/e968df9350723b387a86aeced41a30f0a62a2dc9/mdtraj/geometry/order.py#L164)). `np.einsum` can save time and memory in large matrices, but here we only have 9 entries so there's no point, and it has weird notation.

Since the moments of inertia are vectors originating from zero, the molecule is first centred at the origin.

In [4]:

def compute_com(pts, masses=None):
    """Computes the centre of mass of a point cloud, assuming mass=1"""
    
    if masses is None:
        masses = np.ones(pts.shape[0])
        masses /= masses.sum()
        
    return pts.T.dot(masses).astype('float64')

def calc_m_i(pcl):
    """
    Computes the moment of inertia tensor.
    a more convoluted but easier to understand alternative is in here:
    https://github.com/jwallen/ChemPy/blob/master/chempy/geometry.py
    """
    A = np.sum((pcl**2) * np.ones(pcl.shape[0])[:,None],0).sum()
    B = (np.ones(pcl.shape[0]) * pcl.T).dot(pcl)
    eye = np.eye(3)
    return A * eye - B

In [5]:
#transform to centre of mass:
rect_center = rect - compute_com(rect)

#calculate moment of inertia
mi = calc_m_i(rect_center)
mi

array([[ 35426.06951073,  -3941.93908208, -15226.27832928],
       [ -3941.93908208,  46310.73417837,    713.43176843],
       [-15226.27832928,    713.43176843,  22532.01865892]])

# From this, calculate the principal axes of the moment of inertia:

Essentially, PCA is performed on the moments of intertia tensor. 

In [6]:
def get_pmi(coords):
    """
    Calculate principal moment of inertia
    This code is a re-write of the function from MDAnalysis:
    https://github.com/MDAnalysis/mdanalysis/blob/34b327633bb2aa7ce07bbd507a336d1708871b6f/package/MDAnalysis/core/topologyattrs.py#L1014
    """
    momint = calc_m_i(coords)
    eigvals, eigvecs = np.linalg.eig(momint)
    
     # Sort
    indices = np.argsort(-eigvals) #sorting it returns the 'long' axis in index 0.
    # Return transposed which is more intuitive format
    return eigvecs[:, indices].T


pmi = get_pmi(rect_center)
pmi



array([[ 0.57130489, -0.74681574, -0.34040707],
       [ 0.60366826,  0.66335834, -0.44219945],
       [ 0.55605337,  0.04713777,  0.82980882]])

# Now calculate the angle between one of the coordinate axes (x, y, z) and a principal axis. 

This can be found in a stackoverflow post! https://stackoverflow.com/a/13849249/3089865

This just uses the formula `cos(theta) = v1 . v2 / ( |v1|*|v2|)`. 


In [7]:
def unit_vector(vector):
    """ Returns the unit vector of the vector.  """
    return vector / np.linalg.norm(vector)

def angle_between(v1, v2):
    """ 
    Returns the angle in radians between vectors 'v1' and 'v2'::

            >>> angle_between((1, 0, 0), (0, 1, 0))
            1.5707963267948966
            >>> angle_between((1, 0, 0), (1, 0, 0))
            0.0
    """
    v1_u = unit_vector(v1)
    v2_u = unit_vector(v2)
    return np.arccos(np.clip(np.dot(v1_u, v2_u), -1.0, 1.0))

In [8]:
coord_axis = np.array([1,0,0]) #'x axis'
angle = angle_between(coord_axis, pmi[0])
angle #its in radians

0.9627014496494603

# Calculate the axis about which to rotate in order to align the principal moment of inertia along the coordinate axis
Thankyou to MDAnalysis for this one. The intuition is that when you have two vectors that cross through a point (the origin), then the perpendicular vector to the two vectors can be used to rotate those vectors into each other. 

In [9]:
def rotaxis(a, b):
    """Calculate the vector required in order to rotate `a` to align with `b`
    This is just the normal vector between the two vectors, normalized to unit length"""
    if np.allclose(a, b):
        return np.array([1, 0, 0])
    c = np.cross(a, b)
    return c / np.linalg.norm(c)


In [10]:
rotax = rotaxis(pmi[0], coord_axis)
rotax

array([ 0.        , -0.41475733,  0.90993206])

# Sew it all together
We can use the quaternion rotations from part 1 to actually perform the rotation.


Note: we only do this operation twice! That's because principal axes are orthogonal. Once two principal axes are aligned along two of the coordinate axes, the third is automatically aligned.



In [11]:

rect_aligned = rect_center.copy()


for axidx in range(2):
    #choose an axis to align:
    axis_vector = np.zeros(3)
    axis_vector[axidx] = 1

    ##get pmi:
    pmi = get_pmi(rect_aligned)

    #get angle to that vector
    angle = angle_between(pmi[axidx], axis_vector)
    
    #get axis around which to rotate
    ax = rotaxis(pmi[axidx], axis_vector)

    q = qr.from_axis_angle(ax, -angle) 
    nq = qr.fast_normalise(q)
    rotmat = qr.quaternion_rotation_matrix(nq)

    #rotmat = rotation_matrix(angle, ax)[:3,:3].T

    rect_aligned = rect_aligned.dot(rotmat)


In [12]:

plotly_scatter([rect, rect_aligned], [3, 3])